# Ch 1: Overview
Welcome fellow traders! 

This is a Notebook on the My_Trading_Buddy. The aim of this project is to provide a assistance to a technical approach to trading on the ASX. The goal is for you to be equipt with the necessary tools to analyse market trends and simulate your personalised model! I have broken this up into chapters like a notebook. 

Best of Luck, 

Your trading buddy :)

In [ ]:
#!pip install pandas_datareader datetime math matplotlib pandas numpy fix_yahoo_finance

## Ch 1.1: Import Packages

In [1062]:
#import yfinance as yf
import pandas as pd
from pandas_datareader import data as pdr
import matplotlib.pyplot as plt
import math
import numpy as np

import datetime as dt

import plotly.offline as pyo
import plotly

import plotly.graph_objects as go
from plotly.subplots import make_subplots

pyo.init_notebook_mode(connected=True)
pd.options.plotting.backend = 'plotly'

## Ch 1.2: Scrapping Data and Stock Overview 

In [1191]:
# Define Start and End dates

end = dt.datetime.now()
start  = dt.datetime(2021,6,6)
#end = dt.datetime(2019,12,12)
#start  = dt.datetime(2014,6,6)

In [1225]:
# Define Stocks of interest

stocklist = ['MQG','CBA', 'NAB','ANZ', 'WBC','BOQ','QAN','VAS', 'A200']
#stocklist = ['QAN','MQG','BOQ','ANZ']
stocks = [i + '.AX' for i in stocklist]
#stocklist = ['MQG','CBA']
#stocklist = ['QAN','ATEC','VAS','NDQ']



In [1226]:
# Use the Daily Opening data
import fix_yahoo_finance as yf
df_all = yf.Ticker(stocks, start,end)
df_price = df_all['Open'].copy()
df = df_all['Open'].copy()

# Display Stock Info
print(stocks)
df.plot()

[*********************100%***********************]  9 of 9 completed
['MQG.AX', 'CBA.AX', 'NAB.AX', 'ANZ.AX', 'WBC.AX', 'BOQ.AX', 'QAN.AX', 'VAS.AX', 'A200.AX']


In [1228]:
# Inputs: df with stock prices
# Outputs a rolling normalised df for all stocks

# Normalises using a rolling median
def norm_df_med(df, window = 30, stocks = stocks):
    new_df = pd.DataFrame()
    for stock in stocks:
        new_df[stock] = (df[stock] / (df[stock].rolling(window, min_periods = 0).median()) - 1)
    return new_df

# Normalises using rolling mean
def norm_df_mean(df, window = 30,  stocks = stocks):
    new_df = pd.DataFrame()
    for stock in stocks:
        new_df[stock] = df[stock] / (df[stock].rolling(window, min_periods = 0).mean()-1)
    return new_df

gradient = norm_df_med(df,window = 20, stocks = stocks)
#gradient.plot()

## Ch 1.3 Analysing and Testing Algorithms
Tools that will be used to test algorithms against each other, visualising, graphing etc

Most of these algorithms cannot be tested until later in the notebook


### Ch 1.3a: Results and Comparisons
Compare the final value of 2 algorithms performance

In [1301]:
# Output an array [Coefficient of Variation, Mean, Std]

def final_results(df, stocks = stocks, output = False):
    final_array = []
    for stock in stocks:
        final_array.append(round(df[stock][-1],5))
    if output == True:
        print('Stocks: ',stocks)
        print('Results:',final_array)
        print('Average: {} \261 {}, C_Var: {}'.format(round(np.mean(final_array),2), round(np.std(final_array),2),round(np.mean(final_array)/np.std(final_array),2)))
    return [round(np.mean(final_array)/np.std(final_array),2), round(np.mean(final_array),2), round(np.std(final_array),2)]
#final_results(price_3)

In [1307]:
def compare_results(df_1, df_2, stocks = stocks, mode = 'percentage'):
    df_1_results = []
    df_2_results = []
    for stock in stocks:
        df_1_results.append(round(df_1[stock][-1],6))
        df_2_results.append(round(df_2[stock][-1],6))
    print('Stocks name:', stocks)
    print('Algorithm 1:', df_1_results)
    print('Algorithm 2:', df_2_results)
    stats_comparison = []
    for i in range(len(df_1_results)):
        stats_comparison.append(round(df_1_results[i] - df_2_results[i],6))
    print('Difference :', stats_comparison)
    if mode == 'percentage':
        print('Average    : {} \261 {}%'.format(round(np.mean(stats_comparison),2), round(np.std(stats_comparison),2)))  
    elif mode == 'value':
        print('Average    : ${}'.format(round(np.mean(stats_comparison),2)))
#compare_results(df_1 = price_2, df_2 = bnh, stocks = stocks, mode = 'percentage') 

### Ch 1.3b: Running Bank total
A summary of the highest and lowest percentage of the total wallet, this could affect the ammount of risk your algorithm is under 

In [484]:
def risk_stats(decide = decide_1, df_price = df_price, stocks = stocks, mode = 'value', 
              brokerage_fee = 20, trade_amount = 6000, compound_factor = None, bank = 8000, output = False):
    wallet_df = pd.DataFrame(index = decide.index)
    value_price = trade_price_df(price_df = df_price, decision_trade_df = decide, stocks = stocks, mode = mode,
                   brokerage_fee = brokerage_fee, trade_amount = trade_amount, 
                   compound_factor = compound_factor, bank = bank)
    total_array = []
    for time_index in wallet_df.index:
        total_array.append(sum(sum(value_price[value_price.index == time_index].values)))
    wallet_df['running_total'] = total_array
    wallet_df['running_total'].plot()
    fin = wallet_df['running_total'][-1]/(bank*len(stocks))
    most = wallet_df['running_total'].max()/(bank*len(stocks))
    least = wallet_df['running_total'].min()/(bank*len(stocks))
    if output == True:
        print('Statistics for over-all')
        print('Finishing percentage: {}%'.format(round((fin-1)*100,2)))
        print('Highest Percentage:   {}%'.format(round((most-1)*100,2)))
        #print('Lowest Percentage:   {}%'.format(round((least-1)*100,2)))
    return(wallet_df)

#wallet = risk_stats(decide = decide_2, df_price = df_price, output = True,
#                    compound_factor = compound_factor, bank = bank, trade_amount = amount_per_trade, 
#                    brokerage_fee = brokerage_fee)
1
#wallet.plot()

Trade Output: value
Statistics for over-all
Finishing percentage: 13.3%
Highest Percentage:   13.72%


1

### Ch 1.3c: Plotting Algorithms
Plotting the results of a single algorithm with:
 - Stock Price
 - Transformed Graph (integral)
 - Decision to trade
 - Price of Each Stock
 - Wallet Value 

In [1511]:
def plotting_results(df_price = df_price, integral = integral, decide = decide_1, price = price_1, 
                     stocks = stocks):
    over_all = risk_stats(decide = decide_1, df_price = df_price, compound_factor = 1, output = False)
    cols = plotly.colors.DEFAULT_PLOTLY_COLORS
    k=0
    fig_results = make_subplots(rows = 5, cols = 1, shared_xaxes = True,
                       vertical_spacing = 0.05, subplot_titles = ('Bank Stocks','Normalised Stocks', 'Decisions','Performance','Wallet'),
                       row_width = [1,1,1,1,1])
    fig_results.update_layout(title_text="Graphing",
                  title_font_size=21, autosize = False, width = 800, height = 1000)
    for stock in stocks:
        fig_results.add_trace(go.Scatter(x = df_price.index, y = df_price[stock], name = stock, 
                                           legendgroup = stock, marker=dict(color=cols[k])), row =1, col = 1)
        fig_results.add_trace(go.Scatter(x = df_price.index, y = integral[stock], name = stock, 
                                           showlegend = False, legendgroup = stock, marker=dict(color=cols[k])), row =2, col = 1)
        fig_results.add_trace(go.Scatter(x = df_price.index, y = decide[stock], name = stock, 
                                          showlegend = False, legendgroup = stock, marker=dict(color=cols[k])), row =3, col = 1)
        fig_results.add_trace(go.Scatter(x = df_price.index, y = price[stock], name = stock, 
                                           showlegend = False, legendgroup = stock, marker=dict(color=cols[k])), row =4, col = 1)
        k += 1
    fig_results.add_trace(go.Scatter(x = df_price.index, y = over_all['running_total'], name = 'wallet', 
                                   legendgroup = 'wallet', marker=dict(color=cols[k])), row =5, col = 1)
    final_results(df = price, stocks = stocks, output = True)
    fig_results.show()
#plotting_results(df_price = df_price, integral = integral, decide = decide_1, price = price_1, stock = stocks)
#plotting_results(df_price = df_price, integral = integral, decide = decide_2, price = price_2, stocks = stocks)

Trade Output: value
Stocks:  ['MQG.AX', 'CBA.AX', 'NAB.AX', 'ANZ.AX', 'WBC.AX', 'BOQ.AX', 'QAN.AX', 'VAS.AX', 'A200.AX']
Results: [21.91785, 18.32423, 26.9354, 11.38347, -2.94991, -6.19769, 67.99985, -4.95041, -4.83191]
Average: 14.18 ± 22.56, C_Var: 0.63


In [1274]:
def compare_graphs(df1 = price_1, df2 = price_2, stocks = stocks):
    fig = make_subplots(rows = len(stocks), cols = 1, shared_xaxes = False,
                   subplot_titles = (stocks))
    fig.update_layout(title_text="Comparisons",
                  title_font_size=21, autosize = False, width = 800, height = len(stocks) * 120)
    stock_index = 1
    fig.update_annotations(font_size=15)
    for stock in stocks:
        fig.add_trace(go.Scatter(x=df1.index, y = df1[stock], marker=dict(color = "RoyalBlue"), name = 'df1_'+stock, 
                      legendgroup = stock, showlegend = False), row = stock_index, col = 1)
        fig.add_trace(go.Scatter(x=df1.index, y = df2[stock], marker=dict(color = 'red'), name = 'df2_'+ stock, 
                      legendgroup = stock, showlegend = False), row = stock_index, col = 1)
        stock_index += 1
    compare_results(df_1 = df1, df_2 = df2, stocks = stocks, mode = 'percentage') 
    return(fig.show())
#compare_graphs(df1 = price_1, df2 = bnh, stocks = stocks)

## Ch 2 Standard Trading Models
This section is prebuilt algorithms (from scratch) that are common trading strategies. It is important to compare your proposed model/algorithm against these standards as we want our model to be smarter than the more common trading strategies.

Be sure to use the appropriate Standard model for your assumptions

###  Ch 2.1 Buy and Hold
The Classic buy at the start of your trading period and sell on the last day

This is a very good strategy when you have a large sum of money at the start of your trading period

In [1510]:
def buy_n_hold(p_df, stocks = stocks, mode = 'value', total_investment = 8000, brokerage_fee = 20):
    price_df = p_df
    df = pd.DataFrame(index = p_df.index)
    new_df = df
    
    for stock in stocks:
        initial = price_df[stock][0]
        final = price_df[stock][-1]
        step = (final - initial) / len(new_df)
        value_array = []
        percentage_array = []

        if total_investment != None:
            stock_num = (total_investment - brokerage_fee) / initial
            for day_index in range(len(price_df[stock])):
                current_value = (initial + step * day_index) 
                value_array.append(current_value * stock_num)
                percentage_array.append(((current_value / initial) - 1) * 100)
        elif total_investment == None:
            for day_index in range(len(price_df[stock])):
                current_value = initial + step * day_index
                value_array.append(current_value)
                percentage_array.append(((current_value / initial) - 1) * 100)

        if mode == 'value':
            new_df[stock] = value_array
        elif mode == 'percentage':
            new_df[stock] = percentage_array
    return new_df
bnh = buy_n_hold(p_df = df_price, mode = 'percentage', total_investment = 7000, stocks = stocks)
final_results(bnh, output = True)
#bnh.plot()

Stocks:  ['MQG.AX', 'CBA.AX', 'NAB.AX', 'ANZ.AX', 'WBC.AX', 'BOQ.AX', 'QAN.AX', 'VAS.AX', 'A200.AX']
Results: [17.73481, 5.83418, 17.31072, -14.79775, -10.65218, -22.05731, 35.99468, -2.83533, -1.33621]
Average: 2.8 ± 17.33, C_Var: 0.16


[0.16, 2.8, 17.33]

### Ch 2.2 Dollar Cost Average
A strict stategy where you input the same fixed value for a specific period. The idea is that you purchase more stocks when the market is down, and purchase less stocks when the market is up.

This strategy is good for investors who have a steady stream of income they want to invest in and if the market is continuously going up

In [1509]:
def doll_cost_av(p_df = df_price, day_freq = 60, trade_amount = 5000, stocks = stocks, brokerage_fee = 20, 
                 mode = 'value'):
    new_df = pd.DataFrame(index = p_df.index)
    price_df = p_df
    inv_amount = 0
    inv_array = []
    inv_counter = 0
    for time_index in price_df[stocks].index:
        # trade on the first day
        if len(inv_array) == 0:
            inv_amount += trade_amount
            inv_array.append(inv_amount)
            inv_counter += 1
        elif inv_counter != day_freq: 
            inv_array.append(inv_amount)
            inv_counter += 1
        elif inv_counter == day_freq:
            inv_amount += trade_amount
            inv_array.append(inv_amount)
            inv_counter = 0
    #print(inv_array)
    new_df['invested'] = inv_array

    # dollar cost average
    for stock in stocks:
        price_amount = 0
        price_array = []
        day_counter = 0
        stock_amount = 0
        value_delta_array = []
        for time_index in price_df[stocks].index:
            if len(price_array) == 0:
                price_amount += trade_amount
                #print(stock,time_index,price_df[stock][time_index])
                stock_amount += (trade_amount- brokerage_fee) / price_df[stock][time_index]
                price_array.append(price_amount)
                value_delta_array.append(0)
                day_counter += 1
            elif day_counter != day_freq: 
                price_array.append(stock_amount * price_df[stock][time_index])
                value_delta_array.append(stock_amount * price_df[stock][time_index] - new_df['invested'][time_index])
                day_counter += 1
            elif day_counter == day_freq:
                price_amount += trade_amount
                stock_amount += (trade_amount- brokerage_fee) / price_df[stock][time_index]
                price_array.append(stock_amount * price_df[stock][time_index])
                value_delta_array.append(stock_amount * price_df[stock][time_index] - new_df['invested'][time_index])
                day_counter = 0
            #print(price_amount)
            
        if mode == 'percentage':
            new_df[stock] = ((price_array / new_df['invested']) -1 )* 100 
        elif mode == 'value':
            new_df[stock] = price_array
        elif mode == 'value_delta':
            new_df[stock] = value_delta_array
    if mode == 'percentage' or mode == 'value_delta':
        new_df.drop(columns=['invested'], inplace=True)
    
    return new_df

dca = doll_cost_av(p_df = df, mode = 'percentage', stocks = stocks)
final_results(dca, output = True)
#dca.plot()

Stocks:  ['MQG.AX', 'CBA.AX', 'NAB.AX', 'ANZ.AX', 'WBC.AX', 'BOQ.AX', 'QAN.AX', 'VAS.AX', 'A200.AX']
Results: [1.37801, 7.12636, 7.80185, -6.36467, -0.65246, -13.74976, 26.86028, -1.5257, -0.73725]
Average: 2.24 ± 10.66, C_Var: 0.21


[0.21, 2.24, 10.66]

# Ch 3: Building a New Algorithm

## Ch 3.1: First Algorithm
We standardise each stock performance by dividing it by the rolling median/mean (so we can compare each stock). 

Realising the area under this transformed graph is a better indicator for stock market value. This shows the overall growth of the stock.

Since stock values a year ago is less important information for us than stock values last week, we must include a reduction factor.

We will then put a make a threshold for the new graph and determine when to trade.

In [1507]:
# Inputs: df with stock prices
# Outputs a rolling normalised df for all stocks

# Normalises using a rolling median
def norm_df_med(df, window = 30, stocks = stocks):
    new_df = pd.DataFrame()
    for stock in stocks:
        new_df[stock] = (df[stock] / (df[stock].rolling(window, min_periods = 0).median()) - 1)
    return new_df

# Normalises using rolling mean
def norm_df_mean(df, window = 30,  stocks = stocks):
    new_df = pd.DataFrame()
    for stock in stocks:
        new_df[stock] = df[stock] / (df[stock].rolling(window, min_periods = 0).mean()-1)
    return new_df

gradient = norm_df_med(df,window = 100, stocks = stocks)
#gradient.plot()

In [1508]:
# Inputs: normalised stock prices df
# Outputs: area under the graph with a reduction factor df

def norm_sum_df(df = gradient, reduction_factor  = 1 , stocks = stocks):
    new_df = pd.DataFrame(index = df.index)
    for stock in stocks:
        totals = []
        rolling_sum = 0
        for time_index in df.index:
            rolling_sum = (rolling_sum * reduction_factor + df[stock][time_index])
            totals.append(rolling_sum)
        new_df[stock] = totals
    return new_df
integral = norm_sum_df(df = gradient, reduction_factor = 0.9, stocks = stocks)
#integral.plot()

In [1238]:
# Input: 2 dfs, the first being the transformed df and another being the df with pricing
#        can also input upper and lower threshholds

# Output: df that determines to trade or not based on threshholds
#         also outputs stock price for each given day

def decision_1(integral = integral, df_price = df_price, stocks = stocks, 
               up_thresh = 0.9, low_thresh = 0.25, thresh_window = 180, trig_thresh = 20):
    decisions = pd.DataFrame(index = integral.index)
    for stock in stocks:
        #trim_df = df[df.index > end - start]
        trim_df = integral
        n_df = integral
        #trim_df_price = df_price[df_price.index > end - start]
        trim_df_price = df_price
        #n_df = (trim_df)

        new_df = pd.DataFrame(index = integral.index)
        new_df['price'] = df_price[stock]
        new_df['norm'] = integral[stock]
        new_df['up_bound'] = integral[stock].rolling(thresh_window, min_periods = 0).quantile(up_thresh).copy()
        new_df['low_bound'] = integral[stock].rolling(thresh_window, min_periods = 0).quantile(low_thresh).copy()

        trade = []
        buy_trig, sell_trig = 0, 0   
        cooler_counter = 0
        for time_index in integral[stock].index:
            if integral[stock][time_index] > new_df['up_bound'][time_index] and sell_trig == 0 and cooler_counter > 10:
                sell_trig = 1
                trade.append(1)
            elif integral[stock][time_index] < new_df['low_bound'][time_index] and buy_trig == 0 and cooler_counter > 10:
                buy_trig = 1
                trade.append(-1)
            else:
                trade.append(0)
            cooler_counter+=1

            #Triggers for sell
            if sell_trig < trig_thresh and sell_trig > 0:
                sell_trig += 1
            elif sell_trig == trig_thresh:
                sell_trig = 0

            #Triggers for buy
            if buy_trig < trig_thresh and buy_trig > 0:
                buy_trig += 1
            elif buy_trig == trig_thresh:
                buy_trig = 0 

        new_df['trade'] = trade
        decisions[stock] = trade
    return decisions
decide = decision_1(integral = integral, df_price = df_price, stocks = stocks,up_thresh = 0.6, low_thresh = 0.4, thresh_window = 180,
                    trig_thresh = 20)
#decide.plot()

In [1239]:
def trade_price_df(price_df = df_price, decision_trade_df = df, brokerage_fee = 20, 
                   trade_amount = 6000, compound_factor = None, bank = 8000, mode = 'percentage',
                  stocks = stocks):
    bank_initial = bank
    print('Trade Output:', mode)
    #print(decision_trade_df)
    new_df = pd.DataFrame(index = decision_trade_df.index)

    #if trade_amount > 10000:
    #    brokerage_fee = 30
    for stock in stocks:
        bank = bank_initial
        if compound_factor != None:
            trade_amount = compound_factor * bank
        holding_stocks = 0
        bank_value = []
        total_value = []
        for date_index in decision_trade_df[stock].index:
            if (decision_trade_df[stock][date_index] == -1) & (bank >= trade_amount): 
                # print('buy')
                bank += - trade_amount
                holding_stocks += (trade_amount - brokerage_fee) / price_df[stock][date_index]
                if compound_factor != None:
                    trade_amount = compound_factor * bank
            elif (decision_trade_df[stock][date_index] == 1) and (holding_stocks > 0):
                # print('sell')
                bank += holding_stocks * price_df[stock][date_index] - brokerage_fee
                holding_stocks = 0
                if compound_factor != None:
                    trade_amount = compound_factor * bank
            bank_value.append(bank)
            if math.isnan(price_df[stock][date_index]) == True:
                total_value.append(bank +  holding_stocks * price_df[stock][date_index])
            else:
                total_value.append(bank + holding_stocks * price_df[stock][date_index])
        last_index = -1
        while math.isnan(price_df[stock][last_index]) == True:
            last_index += -1
        else:
            bank_value[-1] = bank + holding_stocks * price_df[stock][last_index]
            #print(stock,bank_value[-21],bank_value[-1])
        
        if mode == 'value':
            new_df[stock] = total_value
        elif mode == 'bank':
            new_df[stock] = bank_value
        elif mode == 'percentage':
            new_df[stock] = ((np.array(total_value) / bank_initial) -1) * 100
    return(new_df)
price_1 = trade_price_df(price_df = df_price, decision_trade_df = decide, stocks = stocks, mode = 'percentage',
                         brokerage_fee = 20, trade_amount = 6000, 
                         compound_factor = 1, bank = 8000)
#price_1.plot()

Trade Output: percentage


### Ch 3.1a: Run Algorithm 1

In [1241]:
stocks_var = stocks
# Gradient
window = 90

# Integral
integral_reduction_factor = 0.90

# Decide
low_thresh = 0.01
up_thresh = 0.6
thresh_window = 150
trade_delay = 30

# Trading
brokerage_fee = 20
compound_factor = 1
amount_per_trade = 6000
bank = 8000
mode = 'percentage'

gradient = norm_df_med(df, window = window, stocks = stocks_var)
integral = norm_sum_df(df = gradient, reduction_factor = integral_reduction_factor, stocks = stocks_var)
decide_1 = decision_1(integral = integral, df_price = df_price, stocks = stocks_var,
                      low_thresh = low_thresh, up_thresh = up_thresh , thresh_window = thresh_window, 
                      trig_thresh = trade_delay)
price_1 = trade_price_df(price_df = df_price, decision_trade_df = decide_1, stocks = stocks_var, mode = mode,
                         brokerage_fee = brokerage_fee, trade_amount = amount_per_trade, 
                         compound_factor = compound_factor, bank = bank)

#final_results(price_1)
#compare_results(df_1 = price_1, df_2 = bnh, stocks = stocks, mode = 'percentage') 
#price_1.plot()
compare_graphs(df1 = price_1, df2 = bnh, stocks = stocks)

Trade Output: percentage
Stocks name: ['MQG.AX', 'CBA.AX', 'NAB.AX', 'ANZ.AX', 'WBC.AX', 'BOQ.AX', 'QAN.AX', 'VAS.AX', 'A200.AX']
Algorithm 1: [-2.454881, 26.085816, 32.6083, 6.31299, 3.006909, 12.729079, 53.121663, 21.186928, 18.788977]
Algorithm 2: [17.734815, 5.834184, 17.310717, -14.797755, -10.652177, -22.05731, 35.994683, -2.83533, -1.33621]
Difference : [-20.189696, 20.251632, 15.297583, 21.110745, 13.659086, 34.786389, 17.12698, 24.022258, 20.125187]
Average    : 16.24 ± 14.12%


### Ch 3.1b: Find Optimal Solution for Algorithm 1
When running for the Optimal Solution consider the variation in the data so you can test the true effictiveness of the algorithm

end = dt.datetime(2023,1,21)
start  = dt.datetime(2021,6,6)

stocklist = ['MQG','CBA', 'NAB','ANZ', 'WBC','BOQ','QAN','VAS', 'A200']
stocks = [i + '.AX' for i in stocklist]


variable_array = []
results_array = []
for i in np.linspace(100,130,num =1):
    print(int(i))
    variable_array.append(i)
    stocks_var = stocks
    # Gradient
    #83 or 90
    #print('window:', int(i))
    window = 83

    # Integral
    #0.69
    integral_reduction_factor = 0.9

    # Decide
    #0.01, 0.57,87
    low_thresh = 0.07
    up_thresh = 0.57
    thresh_window = 120
    trade_delay = 20

    # Trading
    brokerage_fee = 20
    compound_factor = 1
    amount_per_trade = 6000
    bank = 8000
    mode = 'percentage'

    gradient = norm_df_med(df, window = window, stocks = stocks_var)
    integral = norm_sum_df(df = gradient, reduction_factor = integral_reduction_factor, stocks = stocks_var)
    decide_1 = decision_1(integral = integral, df_price = df_price, stocks = stocks_var,
                          low_thresh = low_thresh, up_thresh = up_thresh , thresh_window = thresh_window, 
                          trig_thresh = trade_delay)
    price_1 = trade_price_df(price_df = df_price, decision_trade_df = decide_1, stocks = stocks_var, mode = mode,
                             brokerage_fee = brokerage_fee, trade_amount = amount_per_trade, 
                             compound_factor = compound_factor, bank = bank)
    
    #final_results(price_1)
    results_array.append(final_results(price_1, output = True)[0])

#plt.plot(variable_array, results_array, '-ok', color='black')
#compare_results(df_1 = price_1, df_2 = bnh, stocks = stocks, mode = 'percentage') 

#Average: 21.16 ± 7.73, C_Var: 2.74

# Ch 3.2: Second Algorithm
We will use the standardised rolling median as well as the integral function to work out the best trading pattern.

Using the rolling median graph as the gradient, we can determine when the graph intercepts with the horizontal axis and thus finding the dip of the area graph. Once that has occured we need to set a threshold for the area graph beyond which will trade to remove any uneccesary trades

In [1464]:
# Same as Chapter 2.1

# Inputs: df with stock prices
# Outputs a rolling normalised df for all stocks

# Normalises using a rolling median
def norm_df_med(df = df, window = 30, stocks = stocks):
    new_df = pd.DataFrame()
    for stock in stocks:
        new_df[stock] = (df[stock] / df[stock].rolling(window, min_periods = 0).median() -1)
    return new_df

# Normalises using rolling mean
def norm_df_mean(df = df, window = 30,  stocks = stocks):
    new_df = pd.DataFrame()
    for stock in stocks:
        new_df[stock] = df[stock] / df[stock].rolling(window, min_periods = 0).mean()-1
    return new_df

gradient = norm_df_med(df,window = 10, stocks = stocks)
#gradient.plot()

In [1378]:
# Same as Chapter 2.1

# Inputs: normalised stock prices df
# Outputs: area under the graph with a reduction factor df

def norm_sum_df(df = gradient, reduction_factor  = 1 , stocks = stocks):
    new_df = pd.DataFrame(index = df.index)
    for stock in stocks:
        totals = []
        rolling_sum = 0
        for time_index in df.index:
            rolling_sum = (rolling_sum * reduction_factor + df[stock][time_index])
            totals.append(rolling_sum)
        new_df[stock] = totals
    return new_df
integral = norm_sum_df(df = gradient, reduction_factor = 0.9, stocks = stocks)
#integral.plot()

In [1469]:
def norm_int_df(norm_df, stocks = stocks):
    new_df = pd.DataFrame(index = norm_df.index)
    for stock in stocks:
        crossing_array = []
        for time_index in range(len(norm_df[stock])):
            if time_index == 0:
                crossing_array.append(0)
            elif norm_df[stock][time_index - 1] < 0 and norm_df[stock][time_index] >= 0:
                # indicate to buy
                crossing_array.append(-1)
            elif norm_df[stock][time_index - 1] >= 0 and norm_df[stock][time_index] < 0:
                # indicate to sell
                crossing_array.append(1)
            else: 
                crossing_array.append(0)
        new_df[stock] = crossing_array
    return new_df
intercept = norm_int_df(gradient, stocks = stocks)
intercept.plot()          

In [1471]:
# Input: intercept indicator df and normalised area df
# Output: trade df 
# Gradient = 0, check area graph if its large enough, then buy/sell

def decision_2(norm_int_df = intercept, norm_sum_df = integral, limit_factor = 1, stocks = stocks,
                     trig_thresh = 20):
    new_df = pd.DataFrame(index = norm_int_df.index)
    for stock in stocks:
        trade_array = []
        pos_limit, neg_limit = [],[]
        upper_limit, lower_limit = 0,0
        buy_trig, sell_trig, cooler_counter = 0, 0, 0
        for time_index in range(len(norm_int_df)):
            if norm_sum_df[stock][time_index] > 0:
                pos_limit.append(norm_sum_df[stock][time_index])
                upper_limit = np.mean(pos_limit)
            elif norm_sum_df[stock][time_index] < 0:
                neg_limit.append(norm_sum_df[stock][time_index])
                lower_limit = np.mean(neg_limit)
            #print(norm_int_df[stock][time_index],norm_sum_df[stock][time_index] - (limit_factor * upper_limit))
            #if (norm_sum_df[stock][time_index] > (limit_factor * upper_limit)):#and sell_trig == 0and cooler_counter > 5:
                #print(norm_int_df[stock][time_index],norm_sum_df[stock][time_index] - (limit_factor * upper_limit))
            if norm_int_df[stock][time_index] == 1 and (norm_sum_df[stock][time_index] > (limit_factor * upper_limit)) and sell_trig == 0 and cooler_counter > 5:
                #upper_limit = norm_sum_df[stock][time_index]
                #print(stock,'FIRE')
                trade_array.append(1)
                sell_trig = 1
            elif norm_int_df[stock][time_index] == -1 and (norm_sum_df[stock][time_index] < (limit_factor * lower_limit)) and buy_trig == 0 and cooler_counter > 5:
                #lower_limit = norm_sum_df[stock][time_index]
                #print('tick')
                trade_array.append(-1)
                buy_trig = 1
            else:
                trade_array.append(0)
            
            cooler_counter += 1
               
            #Triggers for sell
            if sell_trig < trig_thresh and sell_trig > 0:
                sell_trig += 1
            elif sell_trig == trig_thresh:
                sell_trig = 0

            #Triggers for buy
            if buy_trig < trig_thresh and buy_trig > 0:
                buy_trig += 1
            elif buy_trig == trig_thresh:
                buy_trig = 0 
        new_df[stock] = trade_array
    return(new_df)
decide_2 = decision_2(norm_int_df = intercept, norm_sum_df = integral, stocks = ['QAN.AX'], limit_factor = 0.32)
#decide_2.plot()

fig_test = make_subplots(rows = 1, cols = 1, shared_xaxes = True,
                       vertical_spacing = 0.05, subplot_titles = ('test'),
                       row_width = [1])
cols = plotly.colors.DEFAULT_PLOTLY_COLORS
k=0
fig_test.update_layout(title_text="Graphing",
                  title_font_size=21, autosize = False, width = 800, height = 400)
for stock in ['QAN.AX']:
    fig_test.add_trace(go.Scatter(x = df_price.index, y = df_price[stock]/5-1, name = stock, 
                                           legendgroup = stock, marker=dict(color=cols[k])), row =1, col = 1)
    fig_test.add_trace(go.Scatter(x = df_price.index, y = gradient[stock], name = stock+'gradient', 
                                           showlegend = True, legendgroup = stock+'gradient', marker=dict(color=cols[k+3])), row =1, col = 1)
    fig_test.add_trace(go.Scatter(x = df_price.index, y = integral[stock], name = stock+'integral', 
                                       showlegend = True, legendgroup = stock+'integral', marker=dict(color=cols[k+1])), row =1, col = 1)
    fig_test.add_trace(go.Scatter(x = df_price.index, y = intercept[stock]/2, name = stock+'intercept', 
                                          showlegend = True, legendgroup = stock+'intercept', marker=dict(color=cols[k+2])), row =1, col = 1)
    k += 1

fig_test.show()

In [1388]:
def trade_price_df(price_df = df_price, decision_trade_df = df, brokerage_fee = 20, 
                   trade_amount = 6000, compound_factor = None, bank = 8000, mode = 'percentage',
                  stocks = stocks):
    bank_initial = bank
    print('Trade Output:', mode)
    #print(decision_trade_df)
    new_df = pd.DataFrame(index = decision_trade_df.index)

    #if trade_amount > 10000:
    #    brokerage_fee = 30
    for stock in stocks:
        bank = bank_initial
        if compound_factor != None:
            trade_amount = compound_factor * bank
        holding_stocks = 0
        bank_value = []
        total_value = []
        for date_index in decision_trade_df[stock].index:
            if (decision_trade_df[stock][date_index] == -1) & (bank >= trade_amount): 
                # print('buy')
                bank += - trade_amount
                holding_stocks += (trade_amount - brokerage_fee) / price_df[stock][date_index]
                if compound_factor != None:
                    trade_amount = compound_factor * bank
            elif (decision_trade_df[stock][date_index] == 1) and (holding_stocks > 0):
                # print('sell')
                bank += holding_stocks * price_df[stock][date_index] - brokerage_fee
                holding_stocks = 0
                if compound_factor != None:
                    trade_amount = compound_factor * bank
            bank_value.append(bank)
            
            if math.isnan(price_df[stock][date_index]) == True:
                total_value.append(bank)
            else:
                total_value.append(bank + holding_stocks * price_df[stock][date_index])
        last_index = -1
        while math.isnan(price_df[stock][last_index]) == True:
            last_index += -1
        else:
            bank_value[-1] = bank + holding_stocks * price_df[stock][last_index]
            #print(stock,bank_value[-21],bank_value[-1])
        
        if mode == 'value':
            new_df[stock] = bank_value
        elif mode == 'bank':
            new_df[stock] = total_value
        elif mode == 'percentage':
            new_df[stock] = ((np.array(total_value) / bank_initial) -1) * 100
    return(new_df)
price_2 = trade_price_df(price_df = df_price, decision_trade_df = decide_2, stocks = stocks, mode = 'percentage',
                         brokerage_fee = 20, trade_amount = 6000, 
                         compound_factor = 1, bank = 8000)
#price_2.plot()

Trade Output: percentage


### Ch 3.2a Run Algorithm 2

In [1493]:
stocks_var = stocks
# Gradient
window = 49

# Gradient
window = 6

# Integral
integral_reduction_factor = 0.65


# Decide
limit_factor = 0.32
trig_thresh = 20

# Trading
brokerage_fee = 20
compound_factor = 1
amount_per_trade = 6000
bank = 8000
mode = 'percentage'

gradient = norm_df_med(df, window = window, stocks = stocks_var)
integral = norm_sum_df(df = gradient, reduction_factor = integral_reduction_factor, stocks = stocks_var)
intercept = norm_int_df(gradient, stocks = stocks)
decide_2 = decision_2(norm_int_df = intercept, norm_sum_df = integral, stocks = stocks, limit_factor = limit_factor, trig_thresh = trig_thresh )
price_2 = trade_price_df(price_df = df_price, decision_trade_df = decide_2, stocks = stocks_var, mode = mode,
                         brokerage_fee = brokerage_fee, trade_amount = amount_per_trade, 
                         compound_factor = compound_factor, bank = bank)

final_results(price_2, output = True)
#plotting_results(df_price = df_price, integral = integral, decide = decide_2, price = price_2, stocks = stocks)
compare_graphs(df1 = price_2, df2 = bnh, stocks = stocks)

Trade Output: percentage
Stocks:  ['MQG.AX', 'CBA.AX', 'NAB.AX', 'ANZ.AX', 'WBC.AX', 'BOQ.AX', 'QAN.AX', 'VAS.AX', 'A200.AX']
Results: [21.91785, 18.32423, 26.9354, 11.38347, -2.94991, -6.19769, 67.99985, -4.95041, -4.83191]
Average: 14.18 ± 22.56, C_Var: 0.63
Stocks name: ['MQG.AX', 'CBA.AX', 'NAB.AX', 'ANZ.AX', 'WBC.AX', 'BOQ.AX', 'QAN.AX', 'VAS.AX', 'A200.AX']
Algorithm 1: [21.917855, 18.324227, 26.935405, 11.383475, -2.949908, -6.197695, 67.999849, -4.950411, -4.831906]
Algorithm 2: [17.734815, 5.834184, 17.310717, -14.797755, -10.652177, -22.05731, 35.994683, -2.83533, -1.33621]
Difference : [4.18304, 12.490043, 9.624688, 26.18123, 7.702269, 15.859615, 32.005166, -2.115081, -3.495696]
Average    : 11.38 ± 11.24%


### Ch 3.2b: Optimise Algorithm 2

end = dt.datetime(2023,1,21)
start  = dt.datetime(2021,6,6)

stocklist = ['MQG','CBA', 'NAB','ANZ', 'WBC','BOQ','QAN','VAS', 'A200']
stocks = [i + '.AX' for i in stocklist]

stocks_var = stocks
variable_array = []
results_array = []
for i in np.linspace(25, 35, num = 1):
    print(int(i))
    variable_array.append(i)
    
    # Gradient
    window = 6

    # Integral
    integral_reduction_factor = 0.65

    # Decide
    limit_factor = 0.32
    trig_thresh = 20

    # Trading
    brokerage_fee = 20
    compound_factor = 1
    amount_per_trade = 6000
    bank = 8000
    mode = 'percentage'

    gradient = norm_df_med(df, window = window, stocks = stocks_var)
    integral = norm_sum_df(df = gradient, reduction_factor = integral_reduction_factor, stocks = stocks_var)
    intercept = norm_int_df(gradient, stocks = stocks)
    decide_2 = decision_2(norm_int_df = intercept, norm_sum_df = integral, stocks = stocks, limit_factor = limit_factor, trig_thresh = trig_thresh)
    price_2 = trade_price_df(price_df = df_price, decision_trade_df = decide_2, stocks = stocks_var, mode = mode,
                             brokerage_fee = brokerage_fee, trade_amount = amount_per_trade, 
                             compound_factor = compound_factor, bank = bank)

    final_results(price_2)
    
    results_array.append(final_results(price_2, output = True)[0])

#plt.plot(variable_array, results_array, '-ok', color='black')
#compare_graphs(df1 = price_2, df2 = bnh, stocks = stocks)

#Average: 14.18 ± 22.56, C_Var: 0.63

### Ch 3.3: Reactive Learning Algorithm
We will still use our rolling gradient algorithm, but this time we will make triggers that change based on input parameters

In [1255]:
# Same as Chapter 2.1

# Inputs: df with stock prices
# Outputs a rolling normalised df for all stocks

# Normalises using a rolling median
def norm_df_med(df, window = 30, stocks = stocks):
    new_df = pd.DataFrame()
    for stock in stocks:
        new_df[stock] = (df[stock] / df[stock].rolling(window, min_periods = 0).median() -1)
    return new_df

# Normalises using rolling mean
def norm_df_mean(df, window = 30,  stocks = stocks):
    new_df = pd.DataFrame()
    for stock in stocks:
        new_df[stock] = df[stock] / df[stock].rolling(window, min_periods = 0).mean()-1
    return new_df

gradient = norm_df_med(df,window = 20, stocks = stocks)
#gradient.plot()

In [1256]:
# Same as Chapter 2.1

# Inputs: normalised stock prices df
# Outputs: area under the graph with a reduction factor df

def norm_sum_df(df = gradient, reduction_factor  = 1 , stocks = stocks):
    new_df = pd.DataFrame(index = df.index)
    for stock in stocks:
        totals = []
        rolling_sum = 0
        for time_index in df.index:
            rolling_sum = (rolling_sum * reduction_factor + df[stock][time_index])
            totals.append(rolling_sum)
        new_df[stock] = totals
    return new_df
integral = norm_sum_df(df = gradient, reduction_factor = 0.9, stocks = stocks)
#integral.plot()

In [1500]:
def integral_bound(integral = integral, stocks = stocks, 
                   high_ratio=0.99, low_ratio= 0.99, sell_with = 0.2, buy_with = 0.2, sell_against = 0.02, buy_against = 0.02):
    new_df = pd.DataFrame(index = integral.index)
    for stock in stocks:
        sell_array = []
        sell_trig = 0
        buy_array = []
        buy_trig = 0
        #high_ratio, low_ratio =0.8, 0.99
        window = 3
        #area_array = [] 
        #area = 0
        for time_index in range(len(integral[stock])):
            # Integral: Positive 
            if integral[stock][time_index] >= 0:
                # Graph > sell_trig
                if integral[stock][time_index] > sell_trig:
                    # Graph going up
                    if time_index != 0 and integral[stock][time_index] > integral[stock][time_index - 1]:
                        sell_trig = (sell_trig * high_ratio  + (integral[stock][time_index])* (sell_with))
                    # Graph going down
                    else:
                        sell_trig = sell_trig * high_ratio + ((integral[stock][time_index])* (sell_with))
                # Graph < sell_trig
                else:#  time_index != 0 and integral[stock][time_index -1] < integral[stock][time_index]:
                    sell_trig = sell_trig * high_ratio + ((integral[stock][time_index])* (sell_against))
                    #print(time_index)
                buy_trig = buy_trig * low_ratio - ((buy_against)*integral[stock][time_index])
            # Integral: Negative
            else:
                # Graph < buy_trig
                if integral[stock][time_index] < buy_trig:
                    # Integral going up
                    if time_index != 0 and integral[stock][time_index] < integral[stock][time_index - 1]:
                        buy_trig = (buy_trig * high_ratio  + integral[stock][time_index]*(buy_with))
                    else:
                        buy_trig = buy_trig * high_ratio + ((integral[stock][time_index])* (buy_against))
                else:#if  time_index != 0 and integral[stock][time_index - 1] > integral[stock][time_index]:
                    buy_trig = buy_trig * high_ratio
                sell_trig = sell_trig * low_ratio - ((sell_against) * integral[stock][time_index])
            sell_array.append(sell_trig)
            buy_array.append(buy_trig)
            
            #area = rolling_ratio * area +  integral[stock][time_index]
            #area_array.append(area)
        new_df[stock] = integral[stock]
        new_df[stock+'_sell_trig'] = sell_array
        new_df[stock+'_buy_trig'] = buy_array
        new_df[stock+'_sell_trig'] = new_df[stock+'_sell_trig'].rolling(window, min_periods = 0).mean()
        new_df[stock+'_buy_trig'] = new_df[stock+'_buy_trig'].rolling(window, min_periods = 0).mean()
    return new_df

integral_b = integral_bound(integral = integral, stocks = stocks)
#print(d)
#integral_b.plot()

In [1501]:
def decision_bound(integral_bound = integral_b, stocks = stocks, trigger_thresh = 20):
    new_df = pd.DataFrame(index = integral_bound.index)
    for stock in stocks:
        trade_array = []
        buy_trig, sell_trig = 0, 0
        trig_thresh = 20
        for time_index in integral[stock].index:
            if integral_bound[stock][time_index] < integral_bound[stock+'_buy_trig'][time_index] and buy_trig == 0:
                trade_array.append(-1)
                buy_trig = 1
            elif  integral_bound[stock][time_index] > integral_bound[stock+'_sell_trig'][time_index] and sell_trig == 0:
                trade_array.append(1)
                sell_trig = 1
            else:
                trade_array.append(0)
            
            #Triggers for sell
            if sell_trig < trig_thresh and sell_trig > 0:
                sell_trig += 1
            elif sell_trig == trig_thresh:
                sell_trig = 0

            #Triggers for buy
            if buy_trig < trig_thresh and buy_trig > 0:
                buy_trig += 1
            elif buy_trig == trig_thresh:
                buy_trig =0
        new_df[stock] = trade_array
    return new_df
decide_3 = decision_bound(integral_bound = integral_b, stocks = stocks, trigger_thresh = 20)
#decide_3.plot()

In [1259]:
# Same as Ch 2.1
def trade_price_df(price_df = df_price, decision_trade_df = df, brokerage_fee = 20, 
                   trade_amount = 6000, compound_factor = None, bank = 8000, mode = 'percentage',
                  stocks = stocks):
    bank_initial = bank
    print('Trade Output:', mode)
    #print(decision_trade_df)
    new_df = pd.DataFrame(index = decision_trade_df.index)

    #if trade_amount > 10000:
    #    brokerage_fee = 30
    for stock in stocks:
        if compound_factor != None:
            trade_amount = compound_factor * bank
        holding_stocks = 0
        bank_value = []
        total_value = []
        for date_index in decision_trade_df[stock].index:
            if (decision_trade_df[stock][date_index] == -1) & (bank >= trade_amount): 
                # print('buy')
                bank += - trade_amount
                holding_stocks += (trade_amount - brokerage_fee) / price_df[stock][date_index]
                if compound_factor != None:
                    trade_amount = compound_factor * bank
            elif (decision_trade_df[stock][date_index] == 1) and (holding_stocks > 0):
                # print('sell')
                bank += holding_stocks * price_df[stock][date_index] - brokerage_fee
                holding_stocks = 0
                if compound_factor != None:
                    trade_amount = compound_factor * bank
            bank_value.append(bank)
            
            if math.isnan(price_df[stock][date_index]) == True:
                total_value.append(bank)
            else:
                total_value.append(bank + holding_stocks * price_df[stock][date_index])
        last_index = -1
        while math.isnan(price_df[stock][last_index]) == True:
            last_index += -1
        else:
            bank_value[-1] = bank + holding_stocks * price_df[stock][last_index]
            #print(stock,bank_value[-21],bank_value[-1])
        
        if mode == 'value':
            new_df[stock] = bank_value
        elif mode == 'bank':
            new_df[stock] = total_value
        elif mode == 'percentage':
            new_df[stock] = ((np.array(total_value) / bank_initial) -1) * 100
    return(new_df)
price_3 = trade_price_df(price_df = df_price, decision_trade_df = decide_3, stocks = stocks, mode = 'percentage',
                         brokerage_fee = 20, trade_amount = 6000, 
                         compound_factor = 1, bank = 8000)
#price_3.plot()

Trade Output: percentage


def plotting_results_testing(df_price = df_price, integral = integral, decide = decide_1, price = price_1, d = d,
                     stock = stocks):
    over_all = risk_stats(decide = decide_1, df_price = df_price, compound_factor = 1, output = False)
    cols = plotly.colors.DEFAULT_PLOTLY_COLORS
    k=0
    fig_results = make_subplots(rows = 2, cols = 1, shared_xaxes = True,
                       vertical_spacing = 0.05, subplot_titles = ('Bank Stocks','d-ml'),#, 'Decisions','Performance','Wallet'),
                       row_width = [1,1])#,1,1,1])
    fig_results.update_layout(title_text="Graphing",
                  title_font_size=21, autosize = False, width = 800, height = 900)
    for stock in stocks:
        fig_results.add_trace(go.Scatter(x = df_price.index, y = df_price[stock], name = stock, 
                                           legendgroup = stock, marker=dict(color=cols[k])), row =1, col = 1)
        #fig_results.add_trace(go.Scatter(x = df_price.index, y = integral[stock], name = stock, 
        #                                   showlegend = False, legendgroup = stock, marker=dict(color=cols[k])), row =2, col = 1)
        fig_results.add_trace(go.Scatter(x = df_price.index, y = d[stock], name = stock, 
                                          showlegend = False, legendgroup = stock, marker=dict(color=cols[k])), row =2, col = 1)
        fig_results.add_trace(go.Scatter(x = df_price.index, y = d[stock+'_sell_trig'], name = stock, 
                                          showlegend = False, legendgroup = stock, marker=dict(color=cols[k+1])), row =2, col = 1)
        fig_results.add_trace(go.Scatter(x = df_price.index, y = d[stock+'_buy_trig'], name = stock, 
                                          showlegend = False, legendgroup = stock, marker=dict(color=cols[k+2])), row =2, col = 1)
        #fig_results.add_trace(go.Scatter(x = df_price.index, y = price_1[stock], name = stock, 
        #                                   showlegend = False, legendgroup = stock, marker=dict(color=cols[k])), row =4, col = 1)
        k += 1
    #fig_results.add_trace(go.Scatter(x = df_price.index, y = over_all['running_total'], name = 'wallet', 
    #                               legendgroup = 'wallet', marker=dict(color=cols[k])), row =5, col = 1)
    fig_results.show()

### Ch 3.3a Run Algorithm 3

In [1480]:
stocks_var = ['QAN.AX','MQG.AX','WBC.AX','NAB.AX','CBA.AX','BOQ.AX','ANZ.AX','VAS.AX','A200.AX']# stocks

# Gradient
window = 65

# Integral
reduction_factor = 0.7

# Integral Bounds
high_ratio = 0.975
low_ratio = 0.96
sell_with = 0.05
buy_with = 0.14
sell_against = 0.01
buy_against = 0.01

# Trading
brokerage_fee = 20
compound_factor = 1
amount_per_trade = 6000
bank = 8000
mode = 'percentage'

gradient = norm_df_med(df,window = window, stocks = stocks_var)
integral = norm_sum_df(df = gradient, reduction_factor = reduction_factor, stocks = stocks_var)
integral_b = integral_bound(integral = integral, stocks = stocks_var, 
                            high_ratio= high_ratio, low_ratio= low_ratio, 
                            sell_with = sell_with, buy_with = buy_with, 
                            sell_against = sell_against, buy_against = buy_against)
decide_3 = decision_bound(integral_bound = integral_b, stocks = stocks_var)
price_3 = trade_price_df(price_df = df_price, decision_trade_df = decide_3, stocks = stocks_var, mode = mode,
                         brokerage_fee = brokerage_fee, trade_amount = amount_per_trade, 
                         compound_factor = compound_factor, bank = bank)
bnh = buy_n_hold(p_df = df_price, mode = 'percentage', total_investment = bank, stocks = stocks)
#price_3.plot()
#print(price_3)
final_results(price_3, stocks = stocks_var, output = True)
#compare_results(df_1 = price_2, df_2 = bnh, stocks = stocks_var, mode = 'percentage') 
#compare_graphs(df1 = price_3, df2 = bnh, stocks = stocks_var)
#integral_b.plot()

Trade Output: percentage
Stocks:  ['QAN.AX', 'MQG.AX', 'WBC.AX', 'NAB.AX', 'CBA.AX', 'BOQ.AX', 'ANZ.AX', 'VAS.AX', 'A200.AX']
Results: [53.40851, 29.477, 3.58755, 37.5819, 13.3213, -8.1181, 8.08484, 0.89659, 0.5053]
Average: 15.42 ± 19.2, C_Var: 0.8


[0.8, 15.42, 19.2]

### Ch 3.3b: Optimise Algorithm 3

end = dt.datetime(2023,1,21)
start  = dt.datetime(2021,6,6)

stocklist = ['MQG','CBA', 'NAB','ANZ', 'WBC','BOQ','QAN','VAS', 'A200']
stocks = [i + '.AX' for i in stocklist]

stocks_var = stocks
variable_array = []
results_array = []
for i in np.linspace(0, 0.02, num = 1):
    print(i)
    variable_array.append(i)
    
    # Gradient
    window = 65

    # Integral
    reduction_factor = 0.7

    # Integral Bounds
    high_ratio = 0.975
    low_ratio = 0.96
    sell_with = 0.05
    buy_with = 0.14
    sell_against = 0.01
    buy_against = 0.01

    # Trading
    brokerage_fee = 20
    compound_factor = 1
    amount_per_trade = 6000
    bank = 8000
    mode = 'percentage'

    gradient = norm_df_med(df,window = window, stocks = stocks_var)
    integral = norm_sum_df(df = gradient, reduction_factor = reduction_factor, stocks = stocks_var)
    integral_b = integral_bound(integral = integral, stocks = stocks_var, 
                                high_ratio= high_ratio, low_ratio= low_ratio, 
                                sell_with = sell_with, buy_with = buy_with, 
                                sell_against = sell_against, buy_against = buy_against)
    decide_3 = decision_bound(integral_bound = integral_b, stocks = stocks_var)
    price_3 = trade_price_df(price_df = df_price, decision_trade_df = decide_3, stocks = stocks_var, mode = mode,
                             brokerage_fee = brokerage_fee, trade_amount = amount_per_trade, 
                             compound_factor = compound_factor, bank = bank)
    final_results(price_3, output = True)
    
    #results_array.append(final_results(price_3, output = True)[0])

#plt.plot(variable_array, results_array, '-ok', color='black')
#compare_graphs(df1 = price_3, df2 = bnh, stocks = stocks)


#Average: 19.12 ± 11.55, C_Var: 1.66

integral_b = integral_bound(integral = integral, stocks = stocks)
compare_results(df_1 = price_1, df_2 = bnh, stocks = stocks, mode = 'percentage') 
plotting_results_testing(df_price = df_price, integral = integral, d = d, price = price_1, stock = stocks)

In [1213]:
array = [0,1,2,3,4]
np.std(array)

1.4142135623730951

## Ch 4: Volatility
Before our trading strategy is based on security, we want to extract high stability stocks such as banks. We will use statistical finance theory to sharpen our search. 

Mid-Velocity trading performs better in High volatility environments. We will desgin an Algorithm to display the volatility and then we can suggest the most appropriate strategy for trading

In [1201]:
log_returns = np.log(df/df.shift(1)).dropna()
daily_std = log_returns.std()
annualised_vol = daily_std * np.sqrt(252) * 100
trading_days = 90
volatility = log_returns.rolling(window = trading_days).std()*np.sqrt(trading_days)
volatility.plot()

In [1202]:
# Sharpe Ratio = average returns/volatility 
Rf = 0.01/252
sharpe_ratio = (log_returns.rolling(window = trading_days).mean() - Rf*trading_days/volatility)
sharpe_ratio.median()

A200.AX   -0.040520
ANZ.AX    -0.030812
BOQ.AX    -0.027946
CBA.AX    -0.029369
MQG.AX    -0.022394
NAB.AX    -0.029821
QAN.AX    -0.017376
VAS.AX    -0.039469
WBC.AX    -0.028503
dtype: float64

In [1203]:
# Sortino volatility
sortino_vol = (log_returns[log_returns<0].rolling(window = trading_days, center = True, min_periods = 10).mean() - Rf*trading_days/volatility)
sortino_ratio = (log_returns.rolling(window = trading_days).mean() - Rf*trading_days/sortino_vol)

In [1204]:
sortino_vol.plot()
sortino_vol.median()

A200.AX   -0.049095
ANZ.AX    -0.041176
BOQ.AX    -0.039572
CBA.AX    -0.039089
MQG.AX    -0.035534
NAB.AX    -0.038863
QAN.AX    -0.033635
VAS.AX    -0.048086
WBC.AX    -0.037251
dtype: float64

In [1205]:
sortino_ratio.median()
#['QAN.AX','MQG.AX','WBC.AX','NAB.AX','CBA.AX',BOQ.AX','ANZ','VAS.AX','A200.AX']

A200.AX    0.072675
ANZ.AX     0.084811
BOQ.AX     0.089434
CBA.AX     0.091447
MQG.AX     0.100118
NAB.AX     0.091892
QAN.AX     0.106274
VAS.AX     0.074032
WBC.AX     0.096711
dtype: float64

In [1198]:
change = (df/df.shift(1)-1)
c = change.dropna()

norm = norm_sum_df(df = c,reduction_factor = .99, stocks = stocks)
norm.plot()



In [439]:
decide = decision_1(integral = norm, df_price = df_price, stocks = stocks,up_thresh = 0.7, low_thresh = 0.05, thresh_window = 60,
                    trig_thresh = 20)
decide.plot()

In [449]:
change = (df/df.shift(1)-1)
c = change.dropna()

norm = norm_sum_df(df = c,reduction_factor = .995, stocks = stocks)
norm.plot()


decide = decision_1(integral = norm, df_price = df_price, stocks = stocks,up_thresh = 0.7, low_thresh = 0.05, thresh_window = 60,
                    trig_thresh = 20)
price_1 = trade_price_df(price_df = df_price, decision_trade_df = decide, stocks = stocks, mode = 'percentage',
                         brokerage_fee = 20, trade_amount = 6000, bank = 8000, compound_factor = 1,)
final_results(price_1)
#plotting_results(df_price = df_price, integral = norm, decide = decide, price = price_1, stock = stocks)
compare_graphs(df1 = price_1, df2 = bnh, stocks = stocks)

Trade Output: percentage
Stocks:  ['ANZ.AX', 'BOQ.AX', 'MQG.AX', 'NAB.AX', 'QAN.AX']
Results: [29.46799, 16.44582, 10.22436, 23.00545, 18.45787]
Average: 19.52
Stocks name: ['ANZ.AX', 'BOQ.AX', 'MQG.AX', 'NAB.AX', 'QAN.AX']
Algorithm 1: [29.467995, 16.445823, 10.224356, 23.005451, 18.457866]
Algorithm 2: [7.345364, -5.901537, 29.849495, 34.263338, 29.160359]
Difference : [22.122631, 22.34736, -19.625139, -11.257887, -10.702493]
Average    : 0.58%


In [450]:
compare_graphs(df1 = price_1, df2 = bnh, stocks = stocks)

Stocks name: ['ANZ.AX', 'BOQ.AX', 'MQG.AX', 'NAB.AX', 'QAN.AX']
Algorithm 1: [29.467995, 16.445823, 10.224356, 23.005451, 18.457866]
Algorithm 2: [7.345364, -5.901537, 29.849495, 34.263338, 29.160359]
Difference : [22.122631, 22.34736, -19.625139, -11.257887, -10.702493]
Average    : 0.58%


# Notes Past This Point

a = trade_list(df, stock = 'NAB.AX', start = dt.timedelta(days = 365))
trading_results(a)['value'].plot()

In [23]:
#a['up_bound'].plot()

In [24]:
fig_test.update_layout(
    title = 'Trading Data',
    xaxis_tickfont_size = 12,
    yaxis = dict(
        title = 'Percentage Gain',
        title_font_size = 14,
        tickfont_size = 12),
    autosize = False,
    width = 800,
    height = 500,
    margin = dict(l = 50, r = 50, b = 100, t = 100, pad =5),
    paper_bgcolor = 'aliceblue'
)

NameError: name 'fig_test' is not defined

## Graphing Multiple graphs

In [ ]:
print(new_df)

In [25]:
import datetime as dt
import pandas as pd
from pandas_datareader import data as pdr
import plotly.offline as pyo
import plotly.graph_objects as go
from plotly.subplots import make_subplots

pyo.init_notebook_mode(connected=True)

In [26]:
end = dt.datetime.now()
start = dt.datetime(2015,1,1)

df = yf.Ticker('CBA.AX', start,end)
df.head

[*********************100%***********************]  1 of 1 completed


<bound method NDFrame.head of                   Open        High         Low       Close   Adj Close  \
Date                                                                     
2015-01-02   84.959686   85.277962   84.661308   85.277962   58.036247   
2015-01-05   85.238182   85.775269   85.049202   85.486832   58.178398   
2015-01-06   84.641411   85.337639   84.412651   84.840332   57.738430   
2015-01-07   84.850281   85.029312   84.094376   84.651360   57.609810   
2015-01-08   85.079041   85.188446   84.671249   84.929848   57.799328   
...                ...         ...         ...         ...         ...   
2023-01-10  102.809998  104.050003  102.599998  103.320000  103.320000   
2023-01-11  103.699997  103.879997  103.000000  103.529999  103.529999   
2023-01-12  104.300003  105.349998  103.790001  105.180000  105.180000   
2023-01-13  105.650002  107.059998  105.589996  106.500000  106.500000   
2023-01-16  106.690002  107.589996  106.330002  107.349998  107.349998   

       

In [27]:
df['MA50'] = df['Close'].rolling(window = 50, min_periods = 0).mean()
df['MA200'] = df['Close'].rolling(window = 200, min_periods = 0).mean()

df['ME30'] = df['Close'].rolling(window = 30, min_periods = 0).median()


In [28]:
fig = make_subplots(rows = 2, cols = 1, shared_xaxes = True,
                   vertical_spacing = 0.1, subplot_titles = ('CBA','Volume'),
                   row_width = [0.2,0.7])

In [29]:
fig.add_trace(go.Candlestick(x = df.index, open= df['Open'], high = df['High'], low = df['Low'], close = df['Close'], 
                             name = 'OHLC'
                            ),row = 1, col = 1)
1

1

In [30]:
fig.add_trace(go.Scatter(x=df.index, y = df['MA50'], marker_color = 'grey', name = 'MA50'), row =1, col = 1)
fig.add_trace(go.Scatter(x=df.index, y = df['MA200'], marker_color = 'lightgrey', name = 'MA200'), row =1, col = 1)
fig.add_trace(go.Scatter(x=df.index, y = df['ME30'], marker_color = 'blue', name = 'ME30'), row =1, col = 1)
1

1

In [31]:
fig.add_trace(go.Bar(x = df.index, y = df['Volume'], marker_color = 'red', showlegend = False), row = 2, col = 1)
1

1

In [32]:
fig.update_layout(
    title = 'CBA historical price chart',
    xaxis_tickfont_size = 12,
    yaxis = dict(
        title = 'Price ($/share)',
        title_font_size = 14,
        tickfont_size = 12),
    autosize = False,
    width = 800,
    height = 500,
    margin = dict(l = 50, r = 50, b = 100, t = 100, pad =5),
    paper_bgcolor = 'aliceblue'
)
1

1

In [33]:
fig.update(layout_xaxis_rangeslider_visible = False)

In [34]:
fig_test = make_subplots(rows = 2, cols = 1, shared_xaxes = True,
                   vertical_spacing = 0.1, subplot_titles = ('CBA','Volume'),
                   row_width = [0.2,0.7])

In [35]:
a=[3,90,3,7,8,100]
if [sum(a)<100]:
    a.append(2)
print(a)

[3, 90, 3, 7, 8, 100, 2]


In [ ]:
a=[3,90,3,7,8,100]
if sum(a)<100:
    a.append(2)
print(a)